In [2]:
from gensim.models import Word2Vec
import numpy as np
import pandas as pd

In [4]:
df = pd.read_csv('wgs_amr.csv')

wgs  AMR  \
0  TCCATGCCCAGCCCGTGCGCGAGCTGGATCACCGCCCGCACGATAG...    0   
1  AGCGCATCAGGCAATTTTGCGTTTGTTTCTGCCTTAAGCAGGTTTA...    0   
2  ATAAATAATAAGTAACTTATTAAATATATACGGAAGCAGGTCTTTT...    0   
3  TGAAAATGCAGAGATAATGGCTAACTGGCATCATCCACGGTTTTTA...    0   
4  GATTATACTCGGTCAGACTTTTCGCCAGTTGAATGCGCCAGTGGAT...    0   
5  CCTTGGCAAGGTCGTGCTCTACCAACTGAGCTATTCCCGCGTACTA...    1   
6  TAAATCTACGCAACAGGTTAGAACCCAAGGCCCGATACGGCATGCG...    1   
7  GGCATAGCGCATCAGGCAGTATTGCATTTATCAGCAGTCTGAATTT...    1   
8  CCTTGGCAAGGTCGTGCTCTACCAACTGAGCTATTCCCGCGTACTA...    1   

                                                kmer  
0  ['TCCATGCCCA', 'CCATGCCCAG', 'CATGCCCAGC', 'AT...  
1  ['AGCGCATCAG', 'GCGCATCAGG', 'CGCATCAGGC', 'GC...  
2  ['ATAAATAATA', 'TAAATAATAA', 'AAATAATAAG', 'AA...  
3  ['TGAAAATGCA', 'GAAAATGCAG', 'AAAATGCAGA', 'AA...  
4  ['GATTATACTC', 'ATTATACTCG', 'TTATACTCGG', 'TA...  
5  ['CCTTGGCAAG', 'CTTGGCAAGG', 'TTGGCAAGGT', 'TG...  
6  ['TAAATCTACG', 'AAATCTACGC', 'AATCTACGCA', 'AT...  
7  ['GGCATAGCGC', 'GCATAGCGCA', 'CATAGCGCAT', 'AT...  
8  ['CCTTGGCAAG', 'CTTGGCAAGG', 'TTGGCAAGGT', 'TG...

In [22]:
kmers_list = df['kmer'].to_list()
w2v_model = Word2Vec(sentences=kmers_list, vector_size=1000, window=5, min_count=1, sg=1, epochs=10)

In [23]:
embedding_dim = 1000
embeddings = df['kmer'].apply(lambda x: sum([w2v_model.wv[k] for k in x]) / len(x))

# Convert embeddings into dataframe
embeddings_df = pd.DataFrame(embeddings.tolist(), index=df.index)

In [24]:
embeddings_df.head()

0         1         2         3         4         5         6    \
0 -0.026660  0.044406 -0.020943  0.040831  0.046513  0.050291  0.027153   
1 -0.024289  0.041548 -0.018660  0.039779  0.042449  0.045781  0.026086   
2 -0.022516  0.039720 -0.016775  0.038900  0.038120  0.041964  0.024716   
3 -0.023651  0.040523 -0.017820  0.039183  0.040944  0.044582  0.025354   
4 -0.024230  0.041846 -0.018105  0.040608  0.041060  0.046145  0.025793   

        7         8         9    ...       990       991       992       993  \
0 -0.020896  0.002697 -0.011320  ... -0.002288  0.005513  0.001389  0.022640   
1 -0.017983  0.002495 -0.012471  ... -0.001945  0.005697  0.000814  0.021817   
2 -0.015213  0.002198 -0.013050  ... -0.001657  0.005784  0.000079  0.021988   
3 -0.017176  0.002259 -0.012558  ... -0.001950  0.005919  0.000432  0.021994   
4 -0.017832  0.002490 -0.012712  ... -0.001930  0.005748  0.000752  0.021802   

        994       995       996       997       998       999  
0  0.011575 -0.005837 -0.012645  0.003255  0.005765  0.006962  
1  0.011243 -0.006035 -0.009894  0.003689  0.005735  0.007876  
2  0.010700 -0.006458 -0.008909  0.004313  0.006012  0.008435  
3  0.011048 -0.006260 -0.010070  0.003938  0.006001  0.008192  
4  0.011282 -0.006051 -0.009826  0.003732  0.005714  0.008021  

[5 rows x 1000 columns]

In [29]:
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

# Combine embeddings with AMR labels
X = embeddings_df
y = df['AMR']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train a Random Forest Classifier
clf = RandomForestClassifier(n_estimators=100, random_state=42)
clf.fit(X_train, y_train)

# Predict on the test set
y_pred = clf.predict(X_test)
print(y_pred)
# Evaluate the model
accuracy = accuracy_score(y_test, y_pred)
print(f'Accuracy: {accuracy}')

[1 0]
Accuracy: 1.0


In [38]:
# Define the new kmer sequence
new_kmer = 'TGTCACGCTGATTGGTATCGTTACAATCTAACGTATCGCCAATGGCCAATGTAAATCCGGCCCGCCTATGGCGAGCCGTTTTGTATGGAAACCAGACCTTATGTTCAAAACGACGCTCTGCGCCTTATTAATTACCGCCTCTTGCTCCACATTTGCTGCCCCTCAACAAATCAACGATATTGTGCATCGCACAATTACCCCGCTTATAGAGCAACAAAAGATCCCCGGTATGGCGGTGGCGGTAATTTATCAGGGTAAACCTTATTACTTTACCTGGGGCTATGCGGACATCGCCAAAAAGCAGCCCGTCACACAGCAAACGTTGTTTGAGTTAGGTTCGGTCAGCAAAACATTTACGGGCGTGCTTGGTGGCGACGCTATTGCTCGAGGGGAAATCAAGTTAAGCGATCCCACAACAAAATACTGGCCTGAACTTACCGCTAAACAGTGGAATGGGATCACACTATTACATCTCGCAACCTACACTGCTGGCGGCCTGCCATTGCAGGTGCCGGATGAGGTGAAATCCTCAAGCGACTTGCTGCGCTTCTATCAAAACTGGCAGCCTACATGGGCGCCAGGAACACAACGTCTGTATGCCAACTCCAGTATCGGTTTGTTCGGCGCACTGGCTGTGAAGCCGTCTGGTTTGAGTTTTGAGCAGGCGATGCAAACACGTGTCTTCCAGCCACTCAAACTCAACCATACGTGGATTAATGTACCTCCCCCAGAAGAAAAGAATTACGCCTGGGGATATCGCGAAGGTAAGGCAGTGCATGTTTCGCCAGGGGCGTTAGATGCTGAAGCTTATGGTGTGAAGTCGACCATTGAAGATATGGCCCGCTGGGTACGAAGCAATATGAATCCCCGTGATATCAACGACAAAACACTTCAGCAAGGGATACAACTGGCACAATCTCGCTACTGGCAAACCGGCGATATGTATCAGGGCCTGGGCTGGGAAATGCTGGACTGGCCGGTAAATCCTGACAGCATCATTAACGGCAGTGGCAATAAAATTGCACTGGCAGCACACCCTGTAAAAGCGATTACGCCCCCAACTCCTGCAGTACGCGCATCATGGGTACATAAAACAGGGGCAACCGGCGGATTTGGTAGCTATGTCGCGTTTATTCCAGAAAAAGAGCTGGGTATAGTGATGCTGGCTAACAAAAACTATCCCAATCCAGCGAGATTCGCCGCCGCCTGGCAGATTCTCAACGCTCTACAGTAA'

def kmer(seq, k):
    return [seq[i:i+k] for i in range(len(seq) - k + 1)]


# Preprocess the new kmer
new_kmer_list = kmer(new_kmer, 10)  # Removed extra brackets

# Get the embeddings for the new kmer, handling KeyErrors
new_kmer_embedding = []
for k in new_kmer_list:
    try:
        new_kmer_embedding.append(w2v_model.wv[k])
    except KeyError:
        # Handle the KeyError - either skip the k-mer or use a default embedding
        # Here, we skip the k-mer and print a warning
        print(f"Warning: K-mer '{k}' not found in vocabulary. Skipping.")
        # Alternatively, you could use a default embedding, like a zero vector:
        # new_kmer_embedding.append(np.zeros(w2v_model.vector_size))

# Calculate average embedding if any valid embeddings were found
if new_kmer_embedding:
    new_kmer_embedding = sum(new_kmer_embedding) / len(new_kmer_embedding)
else:
    # Handle case where no valid embeddings were found
    print("Error: No valid embeddings found for the new k-mer.")
    # You might want to raise an exception or assign a default value here

# Convert the embedding to the appropriate format (e.g., a DataFrame or numpy array)
import numpy as np
new_kmer_embedding_array = np.array(new_kmer_embedding).reshape(1, -1)

# Make a prediction with the trained model
try:
  prediction = clf.predict(new_kmer_embedding_array)
except:
    print('error')

# Output the prediction
amr_value = prediction[0]
print(f'The predicted AMR value for the kmer "{new_kmer}" is {amr_value}')

Error: No valid embeddings found for the new k-mer.
error
The predicted AMR value for the kmer "TGTCACGCTGATTGGTATCGTTACAATCTAACGTATCGCCAATGGCCAATGTAAATCCGGCCCGCCTATGGCGAGCCGTTTTGTATGGAAACCAGACCTTATGTTCAAAACGACGCTCTGCGCCTTATTAATTACCGCCTCTTGCTCCACATTTGCTGCCCCTCAACAAATCAACGATATTGTGCATCGCACAATTACCCCGCTTATAGAGCAACAAAAGATCCCCGGTATGGCGGTGGCGGTAATTTATCAGGGTAAACCTTATTACTTTACCTGGGGCTATGCGGACATCGCCAAAAAGCAGCCCGTCACACAGCAAACGTTGTTTGAGTTAGGTTCGGTCAGCAAAACATTTACGGGCGTGCTTGGTGGCGACGCTATTGCTCGAGGGGAAATCAAGTTAAGCGATCCCACAACAAAATACTGGCCTGAACTTACCGCTAAACAGTGGAATGGGATCACACTATTACATCTCGCAACCTACACTGCTGGCGGCCTGCCATTGCAGGTGCCGGATGAGGTGAAATCCTCAAGCGACTTGCTGCGCTTCTATCAAAACTGGCAGCCTACATGGGCGCCAGGAACACAACGTCTGTATGCCAACTCCAGTATCGGTTTGTTCGGCGCACTGGCTGTGAAGCCGTCTGGTTTGAGTTTTGAGCAGGCGATGCAAACACGTGTCTTCCAGCCACTCAAACTCAACCATACGTGGATTAATGTACCTCCCCCAGAAGAAAAGAATTACGCCTGGGGATATCGCGAAGGTAAGGCAGTGCATGTTTCGCCAGGGGCGTTAGATGCTGAAGCTTATGGTGTGAAGTCGACCATTGAAGATATGGCCCGCTGGGTACGAAGCAATATGAATCCCCGTGATATCAACGACAAAACACTTCAGCAAGGGATA